In [0]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go

In [0]:
df = spark.read.table("ds_internal_tables.reverse_lookup_sample_cosine").toPandas()

In [0]:
def dcision_from_ip(ip,threshold):
        Lambda = (1-threshold)/np.log(0.5)
        passed = np.exp((1-ip)/Lambda)
        return passed


In [0]:
threshold=0.79
df['ip_sum_exp'] = df['values'].apply(lambda items_list:np.sum([dcision_from_ip(item['ip'],threshold=threshold)*item['count'] for item in items_list]))
df['ip_avg_exp'] = df['ip_sum_exp']/df['counts']
df['passed_threhsold'] = df.apply(lambda row:np.sum([value['count'] for value in row['values'] if value['ip']>threshold])/row['counts'],axis=1)
df['values'] = df['values'].apply(lambda x:sorted(x, key=lambda d: d['count'])[::-1])

In [0]:
tmp = df.sample(n=10000)
def dcision_line(passed_threhsold,ip_avg,threshold):
    passed = (passed_threhsold+ip_avg)/2
    return passed

tmp['pass'] = tmp.apply(lambda x:dcision_line(x['passed_threhsold'],x['ip_avg_exp'],threshold)>0.5,axis=1)
x = np.linspace(min(tmp['ip_avg_exp'].to_list())-0.05,max(tmp['ip_avg_exp'].to_list())+0.05,num=50)
y = np.linspace(min(tmp['passed_threhsold'].to_list())-0.05,max(tmp['passed_threhsold'].to_list())+0.05,num=50)
z = [[1 if dcision_line(y_i,x_i,threshold)>0.5 else 0 for x_i in x] for y_i in y]

In [0]:
fig = go.Figure()
tmp1 = tmp.loc[tmp['lookup_result']>-0.5]
tmp2 = tmp.loc[tmp['lookup_result']<-0.5]
text1 = [[f'{k} : {v}</br>' for dic in dics for k,v in dic.items()] for full_name,dics in zip(tmp1['full_name'].to_list(),tmp1['values'].to_list())]
text2 = [[f'{k} : {v}</br>' for dic in dics for k,v in dic.items()] for full_name,dics in zip(tmp2['full_name'].to_list(),tmp2['values'].to_list())]
colorscale = [[0, 'red'],  [1, 'green']]
fig.add_trace(go.Contour(z=z,
        x=x, # horizontal axis
        y=y, # vertical axis
        colorscale=colorscale,
        showscale=False
    ))
fig.add_trace(go.Scatter(x=tmp1['ip_avg_exp'],y=tmp1['passed_threhsold'],text=text1,
                         hovertemplate = ["full name: {:}<br>lookup score: {:}<br> data:<br>{:} <br>passed threshold: {:} </br> average cosine similarity : {:}</br> decision : {:}".format(full_name,lookup,text_i,y_i,x_i,passed) for full_name,lookup,text_i,x_i,y_i,passed in zip(tmp1['full_name'].to_list(),tmp1['lookup_result'].to_list(),text1,tmp1['ip_avg_exp'].to_list(),tmp1['passed_threhsold'].to_list(),tmp1['pass'].to_list())],
                         mode='markers',name='Samples lookup score > -0.5',marker=dict(color='blue')))
fig.add_trace(go.Scatter(x=tmp2['ip_avg_exp'],y=tmp2['passed_threhsold'],text=text2,
                         hovertemplate = ["full name: {:}<br>lookup score: {:}<br>data:<br>{:} <br>passed threshold: {:} </br> average cosine similarity : {:}</br> decision : {:}".format(full_name,lookup,text_i,y_i,x_i,passed) for full_name,lookup,text_i,x_i,y_i,passed in zip(tmp2['full_name'].to_list(),tmp2['lookup_result'].to_list(),text2,tmp2['ip_avg_exp'].to_list(),tmp2['passed_threhsold'].to_list(),tmp2['pass'].to_list())],
                         mode='markers',name='Samples lookup score < -0.5',marker=dict(color='black')))

# fig.add_trace(go.Scatter(x=[0.5,1.1],y=[0.5,0.5],mode='lines',line_color='red',name='decision line'))
fig.update_layout(height=1000,width=1250,coloraxis_showscale=False,
                  xaxis=dict(title='exponential similarity',range=[min(x),max(x)]),
                  yaxis=dict(title='ratio of times passed threshold',range=[min(y),max(y)]))
# fig.update_traces(showscale=False)
# fig.write_html(f'/dbfs/mnt/{project_dir[5:]}/results/decision_making')
fig.show()